# エンドツーエンドのコードファースト生成AIエクスペリメント

このノートブックでは、DataRobotが提供する生成AI機能の包括的な概要を説明します。このノートブックでは、DataRobot Pythonクライアントの[Experimentalバージョン](https://datarobot-public-api-client.readthedocs-hosted.com/en/early-access/)に含まれるメソッドを使用しています。実験的なDataRobot Pythonライブラリへのアクセスについては、DataRobotの担当者または管理者にお問い合わせいただくか、`pip install datarobot-early-access`を使用してください。

以下のセルは使用例を示しています。

In [ ]:
See the following code block for example usage:

import datarobot as dr
from datarobot._experimental.models.genai.vector_database import VectorDatabase
from datarobot._experimental.models.genai.vector_database import ChunkingParameters
from datarobot._experimental.models.enums import VectorDatabaseEmbeddingModel
from datarobot._experimental.models.enums import VectorDatabaseChunkingMethod
from datarobot._experimental.models.genai.playground import Playground
from datarobot._experimental.models.genai.llm import LLMDefinition
from datarobot._experimental.models.genai.llm_blueprint import LLMBlueprint
from datarobot._experimental.models.genai.llm_blueprint import VectorDatabaseSettings
from datarobot._experimental.models.genai.chat_prompt import ChatPrompt
from datarobot._experimental.models.genai.vector_database import CustomModelVectorDatabaseValidation
from datarobot._experimental.models.genai.comparison_prompt import ComparisonPrompt
from datarobot._experimental.models.genai.custom_model_llm_validation import CustomModelLLMValidation

### ユースケースを作成

生成AIはDataRobotのユースケースの中で機能するので、新しいユースケースを作成することから始めます。

In [ ]:
use_case = dr.UseCase.create()

このワークフローでは、GenAIモデルでベクターデータベースを使用します。次に、一連のドキュメントを含むデータセットをアップロードします。

In [ ]:
dataset = dr.Dataset.create_from_file("resumes.zip")

### ベクターデータベースの作成

In [ ]:
chunking_parameters = ChunkingParameters(
    embedding_model=VectorDatabaseEmbeddingModel.JINA_EMBEDDING_T_EN_V1,
    chunking_method=VectorDatabaseChunkingMethod.RECURSIVE,
    chunk_size=128,
    chunk_overlap_percentage=25,
    separators=[],
)
vdb = VectorDatabase.create(dataset.id, chunking_parameters, use_case)

以下のセルを使ってベクターデータベースを取得し、それが完了していることを確認します。

In [ ]:
vdb = VectorDatabase.get(vdb.id)
assert vdb.execution_status == "COMPLETED"

### LLMプレイグラウンドの作成

大規模言語モデル（LLM）をホストするLLMプレイグラウンドを作成します。

In [ ]:
playground = Playground.create(name="New playground for example", use_case=use_case)

以下のセルを使って、使用可能なLLMの種類を確認します。デフォルトでは、このメソッドは読みやすいようにdictとして返します。これには、各LLMで使用できる設定のリストと、値に対する制約が含まれます。

In [ ]:
llms_dict = LLMDefinition.list()
print(llms_dict)

例として、GPT 3.5を使用します。

In [ ]:
llms = LLMDefinition.list(as_dict=False)
gpt = llms[0]

GPTと対話するには、希望の設定でLLMブループリントを作成する必要があります。使用できる設定はLLMのタイプによって異なるため、ブループリントの作成時に検証される値を含む一般的なdictを取ります。GPTで使用できる設定を確認します。

In [ ]:
print([setting.to_dict() for setting in gpt.settings])

### LLMブループリントの作成

In [ ]:
llm_settings = {
    "system_prompt": (
        "You are a pirate who begins each response with 'Arrr' "
        "and ends each response with 'Matey!'"
    ),
    "max_completion_length": 256,  # Let's ask for short responses
    "temperature": 2.0,  # With a high degree of variability
}

データベース作成時のデフォルトとは異なるベクターデータベース設定を使用します。

In [ ]:
vector_database_settings = VectorDatabaseSettings(
    max_documents_retrieved_per_prompt=2,
    batch_size=32,
    max_tokens=128,
)

llm_blueprint = LLMBlueprint.create(
    playground=playground,
    name="GPT",
    llm=gpt,
    llm_settings=llm_settings,
    vector_database=vdb,
    vector_database_settings=vector_database_settings,
)

### LLMブループリントとのチャット

以下のセルを使って、LLMブループリントとチャットします。

In [ ]:
prompt1 = ChatPrompt.create(
    llm_blueprint,
    "How can a pirate resume be evaluated?",
    wait_for_completion=True,
)
print(prompt1.result_text)

上のセル例は、`result_metadata`によって確認された、切り捨てられた出力を返します。

In [ ]:
print(prompt1.result_metadata.error_message)

`max_completion_length`を大きくして、もう一度チャットしてみます。LLM設定は、LLMブループリントがまだ保存されていない限り、チャットプロンプト内で更新できます。そうすることで、LLMブループリントの基本設定が更新されます。

In [ ]:
llm_settings["max_completion_length"] = 1024
prompt2 = ChatPrompt.create(
    llm_blueprint,
    "Please answer the previous question again.",
    llm_settings=llm_settings,
    wait_for_completion=True,
)
print(prompt2.result_text)

新しい`max_completion_length`を維持して、LLMブループリントが更新されたことを確認できます。

In [ ]:
llm_blueprint = LLMBlueprint.get(llm_blueprint.id)
print(llm_blueprint.llm_settings)

回答が満足のいくものでないかもしれないため、次はTemperatureを下げて回答を修正します。

In [ ]:
llm_settings["temperature"] = 0.8
prompt3 = ChatPrompt.create(
    llm_blueprint,
    "Please summarize the best pirate resume.",
    llm_settings=llm_settings,
    wait_for_completion=True,
)
print(prompt3.result_text)

LLMがベクターデータベースの情報を使用していることを確認します。

In [ ]:
print([citation.text for citation in prompt3.citations])

LLMブループリントを保存して、設定を固定し、比較プロンプトで使えるようにします。

In [ ]:
llm_blueprint = llm_blueprint.update(is_saved=True)

次に、既存のLLMブループリントから新しいLLMブループリントを作成し、いくつかの設定を変更して2つを比較します。

In [ ]:
new_llm_blueprint = LLMBlueprint.create_from_llm_blueprint(llm_blueprint, name="new blueprint")

新しいブループリントからベクターデータベースを削除し、以下のように設定を変更して、ブループリントを保存します。

In [ ]:
llm_settings["system_prompt"] = "You are an AI assistant who helps to evaluate resumes."
new_llm_blueprint = new_llm_blueprint.update(
    llm_settings=llm_settings,
    remove_vector_database=True,
    is_saved=True,
)

LLMブループリントを[DataRobot UIから](https://docs.datarobot.com/ja/docs/gen-ai/deploy-llm.html)デプロイできます。

### カスタムモデルのベクターデータベースを追加する

デプロイからカスタムモデルのベクターデータベースを追加します。この例では、以前にデプロイされたテキスト生成モデルを使用します。ベクターデータベースとして使用できるように検証します。

In [ ]:
custom_model_vdb_validation = CustomModelVectorDatabaseValidation.create(
    prompt_column_name="prompt",
    target_column_name="response",
    deployment_id="652da8617f7054ab1a0719a8",
    wait_for_completion=True,
)
assert custom_model_vdb_validation.validation_status == "PASSED"

In [ ]:
# Now create a vector database
custom_model_vdb = VectorDatabase.create_from_custom_model(
    name="custom model vdb",
    use_case=use_case,
    validation_id=custom_model_vdb_validation.id,
)
custom_model_vdb = VectorDatabase.get(custom_model_vdb.id)
assert custom_model_vdb.execution_status == "COMPLETED"

### カスタムモデルのLLMを追加する

次に、デプロイからカスタムモデルLLMを追加します（カスタムモデルLLMの作成は、このワークフローの対象外です）。LLMとして使用するテキスト生成モデルを検証します。

In [ ]:
custom_model_llm_validation = CustomModelLLMValidation.create(
    prompt_column_name="prompt",
    target_column_name="response",
    deployment_id="652da8617f7054ab1a0719a8",
    wait_for_completion=True,
)
assert custom_model_llm_validation.validation_status == "PASSED"

カスタムモデルLLMとカスタムモデルベクターデータベースを使ってLLMブループリントを作成できるようになりました。

In [ ]:
custom_model_llm_blueprint = LLMBlueprint.create(
    playground=playground,
    name="custom model LLM with custom model vdb",
    llm="custom-model",
    llm_settings={"validation_id": custom_model_llm_validation.id},
    vector_database=custom_model_vdb,
)

比較で使用できるように、カスタムモデルのブループリントを保存します。

In [ ]:
custom_model_llm_blueprint = custom_model_llm_blueprint.update(is_saved=True)

LLMブループリントを比較できるようになりました。

In [ ]:
comparison_prompt = ComparisonPrompt.create(
    [llm_blueprint, new_llm_blueprint, custom_model_llm_blueprint],
    "Summarize the best resume",
    wait_for_completion=True,
)
print([result.result_text for result in comparison_prompt.results])